In [5]:
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime as dt
import time

username = 'jizhaobridgeport@gmail.com'
password = '12345shift'

def login():
    rh.login(username, password)


In [6]:

 
 


def open_market():
    from datetime import datetime

    market = False
    time_now =datetime.now().time()
    import datetime
    market_open = datetime.time(9,30,0) # 9:30AM
    market_close = datetime.time(15,59,0) # 3:59PM

    if time_now > market_open and time_now < market_close:
        market = True
    else:
        pass

    return(market)

#def logout():
   # rh.authentication.logout()
def get_cash():
    rh.login(username, password)
    rh_profile = rh.load_account_profile()
    cash = float(rh_profile['portfolio_cash'])
    return cash



def get_holdings_and_bought_price(stocks):
    holdings = {stocks[i]: 0 for i in range(0, len(stocks))}
    bought_price = {stocks[i]: 0 for i in range(0, len(stocks))}
    rh_holdings = rh.account.build_holdings()

    for stock in stocks:
        try:
            holdings[stock] = int(float((rh_holdings[stock]['quantity'])))
            bought_price[stock] = float((rh_holdings[stock]['average_buy_price']))
        except:
            holdings[stock] = 0
            bought_price[stock] = 0

    return(holdings, bought_price)
#holdings, bought_price = get_holdings_and_bought_price(stocks)
def sell(stock, holdings):
    print('### Trying to SELL {} at ${}'.format(stock, price))
def buy(stock, allowable_holdings):
      buy_order = rh.orders.order_buy_fractional_by_price(stock,
                                       allowable_holdings,
                                        timeInForce='gfd',
                                        extendedHours=False)
      print('### Trying to BUY {} at ${}'.format(stock, price))

def build_dataframes(df_trades, trade_dict, df_prices, price_dict):
    import datetime as dt
    time_now = str(dt.datetime.now().time())[:8]
    df_trades.loc[time_now] = trade_dict
    df_prices.loc[time_now] = price_dict
    return(df_trades, df_prices)

def get_historical_prices(stocks):
    def price_5mins(stock):
            from datetime import datetime as dt
            api_key = '86dd63f6b8ae774b061232685b78eb52'
            today = dt.today()
            a=str(today.year)
            b=str(today.month)
            c=str(today.day)
            d=str(today.day-1)
            e=int(today.day)
            start = a +'-'+ b +'-'+d
            end =a +'-'+ b +'-'+c
            bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-chart/5min/{stock}?from={start}&to={end}&apikey={api_key}').json()
      #      print(bs)  # 新增打印语句
            df = pd.DataFrame(bs)
            df = pd.DataFrame(bs)
            df['date'] = pd.to_datetime(df['date'])  # 新增       
            dates_times = pd.to_datetime(df.loc[:, 'date'])
            close_prices = df.loc[:, 'close'].astype('float')
   
            df_price = pd.concat([close_prices, dates_times], axis=1)
            df_price = df_price.set_index('date')
            df_price1 = df_price.loc[(df_price.index.day==e),:]
        #    df_price = df_price.iloc[date, :]
            df_price1 = df_price1.rename(columns={'close': stock})
            df_price1 =df_price1.sort_index()
            return df_price1
   
      #stocks=['LHX']
       
    def close_price(stock):
        from datetime import datetime as dt
        import datetime
        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        today = dt.today()
        a=str(today.year)
        b=str(today.month)
        c=str(today.day-1)
        d = str(today.day-2)
        start = a +'-'+ b +'-'+d
        end =a +'-'+ b +'-'+c
        bs1 = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{stock}?from={start}&to={end}&apikey={api_key}').json()
       # print(bs1)  # 新增打印语句
        df_1 = pd.DataFrame(bs1['historical'])
        df_1['date'] = pd.to_datetime(df_1['date'])  # 新增
       # stock = pd.DataFrame(bs)
        df_1 =df_1[['date','open','high','low','close','volume']]
        dates = pd.to_datetime(df_1.loc[:, 'date'])
        close= df_1.loc[:, 'close'].astype('float')
        df_2 = pd.concat([close, dates], axis=1)
        #= df_2.iloc[:10, :]
        df_2 = df_2.rename(columns={'close': stock})
        df_2 = df_2.set_index('date')
       # df_2 = df_2.sort_index()
        return df_2
   
    df_close = pd.DataFrame()
    for stock in stocks:
      #  print(stock)      
        df_price2 =  close_price(stock)
        df_close = pd.concat([df_close,df_price2], axis =1)
        df_close=  df_close.sort_index(ascending=False)
   # stocks = ['AAPL']
    df_price = pd.DataFrame()
    for stock in stocks:  
        print(stock)
        df_price1 =  price_5mins(stock)
        df_price = pd.concat([df_price,df_price1], axis =1)
     
#stock = 'AAPL'        
    final_data1 = pd.DataFrame()
    for stock in stocks:
        price_5min =  df_price[stock][1]
        price_10min =  df_price[stock][2]
        close_p = df_close[stock][0]
        pct_change =  ((price_10min-close_p)/ close_p) *100
       
        final_data = pd.DataFrame(columns = ['price_5min','price_10min','close_p','pct_change'])
        a = [{'price_5min':price_5min, 'price_10min':price_10min ,'close_p':close_p,'pct_change':pct_change}]
        final_data = pd.concat([final_data, pd.DataFrame.from_records(a)], ignore_index=True)
        #final_data = final_data.append({'price_5min':price_5min, 'price_10min':price_10min ,'close_p':close_p,'pct_change':pct_change}, ignore_index = True)
        final_data  =final_data .T
        final_data = final_data.rename(columns = {0:stock})
        final_data1  =pd.concat([final_data1 ,final_data], axis =1)
#        final_data1['pct_change'] =round( final_data1['price_10m']/final_data1['close_p'],2)
    return final_data1
#stocks = final_trade_stock    


def final_trade_stock(stocks):
    final_data1 = get_historical_prices(stocks)
    trade_stock = []
    for stock in stocks:
        if final_data1[stock]['price_5min'] <= final_data1[stock]['price_10min'] and final_data1[stock]['price_10min'] >= final_data1[stock]['close_p']:
            trade_stock.append(stock)
     
    f = pd.DataFrame(final_data1[trade_stock])
    final_trade_stock = []
    for t in f.columns:
            if 0 <f[t]['pct_change']<5:
                final_trade_stock .append(t)
    return final_trade_stock
   
from datetime import datetime as dt
import datetime
today = dt.today()
a = str(today.year)
b = str(today.month)
c = str(today.day)
open_market()
#ticker_sum.remove('AFG')
print('Buying power before making trade:')
print(get_cash())
#stocks  =['COST','LHX']
stocks= final_trade_stock(ticker_sum)
#stocks = final_trade_stock
#ticker_sum = l    
#print('stocks:', stocks)
l = len(stocks)
print(l)
myCash = get_cash()
cash =myCash
myCash = 0

print('Buying power:')
print(cash)

trade_dict = {stocks[i]: 0 for i in range(0, len(stocks))}
price_dict = {stocks[i]: 0 for i in  range(0, len(stocks))}
df_trades = pd.DataFrame(columns=stocks)
df_prices = pd.DataFrame(columns=stocks)
#stocks = ['AAPL','FB']
   # while open_market():
prices = rh.stocks.get_latest_price(stocks)
holdings, bought_price = get_holdings_and_bought_price(stocks)
#print('holdings:', holdings)

for i, stock in enumerate(stocks):
    price = float(prices[i])
    print('{} = ${}'.format(stock, price))
    it =len(stocks)
    allowable_holdings =  round(cash/it,1)
    #if holdings[stock] == 0:
    buy(stock, allowable_holdings)

 
from datetime import datetime as dt
import datetime
today = dt.today()
a = str(today.year)
b = str(today.month)
c = str(today.day)
m = pd.DataFrame(stocks)

myCash = get_cash()
cash =myCash  
# cash =000
print('Buying power after making trade:')
print(cash)





Buying power before making trade:
ERROR: There was an issue loading pickle file. Authentication may be expired - logging in normally.
-86521.65


NameError: name 'ticker_sum' is not defined

In [7]:
#code for selling manually。。。ticker_sum ='EGLE'
my_stocks = rh.build_holdings()
df =pd.DataFrame(my_stocks).T
df1 =df[['price','quantity','average_buy_price','percent_change']]
df1

400 Client Error: Bad Request for url: https://api.robinhood.com/fundamentals/?symbols=SBRCY
400 Client Error: Bad Request for url: https://api.robinhood.com/quotes/?symbols=SBRCY


price      quantity average_buy_price percent_change
DIS     85.240000  153.03529400           94.6705          -9.96
BA     196.350000   36.00000000          226.4072         -13.28
AMZN   132.250100   35.00000000          130.3323           1.47
GOOGL  141.220000   45.00000000          126.0278          12.05
ISRG   281.990000   13.00000000          308.6831          -8.65
TSLA   262.790000   35.03844100          234.0256          12.29
MSFT   331.000000   35.00000000          325.5917           1.66
AAPL   180.360000   45.02679000          178.2561           1.18
U       30.310000  100.00000000           40.6444         -25.43
JNJ    156.220000   65.00000000          163.1847          -4.27
ADBE   549.910000    5.00000000          540.6840           1.71
TSM     92.000000   85.00000000          100.6801          -8.62
CVS     71.740000   65.00000000           73.8768          -2.89
BAC     27.060000  100.00000000           30.3778         -10.92
SHOP    54.350000   25.00000000           56.2392          -3.36
HD     298.500000   25.00000000          324.9700          -8.15
GS     313.150000   15.00000000          348.9660         -10.26
ETSY    64.860000  130.00000000           89.3914         -27.44
UNH    524.130000    3.00000000          473.6500          10.66
INTU   541.580000    8.00000000          505.2463           7.19
ACN    312.540000    5.00000000          315.5160          -0.94

In [ ]:
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime as dt
import time

username = 'jizhaobridgeport@gmail.com'
password = '12345shift'

def login():
    rh.login(username, password)

def get_stop(stock):# pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = ( today-datetime.timedelta(1)).strftime('%Y-%m-%d') 
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        tick = ticker
        last_day.index = [tick]
        last_day['stop_loss'] = (last_day['vol_down2'] +last_day['vol_down3'] )/2
        last_day['stop_loss_pct'] = (last_day['Close']- last_day['stop_loss'])/last_day['Close']*100
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] +last_day['Close'][-1] )/2

        return last_day
    
def get_trailing_stop_percentage(stock):
    stop_price = get_stop(stock)['stop_loss'][0]
    current_price = all_data1['price'][stock]
    trailing_percentage = (current_price - stop_price) / current_price
    return trailing_percentage * 0.2  # Use 20% of the calculated stop percentage

login()

sold_half = set()  # Track stocks that we have sold half of

while True:
    my_stocks = rh.build_holdings()
    df = pd.DataFrame(my_stocks).T
    df1 = df[['price', 'quantity', 'average_buy_price', 'percent_change']]
    stock = df1.index.tolist()
    all_data = pd.DataFrame()

    for ticker in stock:
        print(ticker)
        last_day = get_stop(ticker)
        all_data = pd.concat([all_data, last_day], axis=0)

    all_data = all_data[['stop_loss']]
    all_data1 = df1.merge(all_data, left_index=True, right_index=True)
    all_data1['price'] = all_data1['price'].astype(float)
    all_data1['pct_cha'] = ((all_data1['price'] - all_data1['stop_loss']) / all_data1['price']) * 100

    import random
    x = random.random()
    y = float((x + 5) / 100)
    z = float((10 - x) / 100)
    all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
    all_data1['target_price1'] = all_data1['average_buy_price'] * (1 + y)
    all_data1['target_price2'] = all_data1['average_buy_price'] * (1 + z)

    trailing_stop_percentages = {}
    for s in all_data1.index.tolist():
        trailing_stop_percentages[s] = get_trailing_stop_percentage(s)

    for s in all_data1.index.tolist():
        current_price = all_data1['price'][s]
        quantity = float(all_data1['quantity'][s])
        trailing_stop_price = current_price * (1 - trailing_stop_percentages[s])

        if current_price >= all_data1['target_price1'][s] and s not in sold_half:
            quantity1 = math.ceil(quantity / 2)  # sell half
            rh.orders.order_sell_market(symbol=s, quantity=quantity1, timeInForce='gfd')
            print(f"First target price reached for {s}, selling half at market price.")
            sold_half.add(s)  # Add the stock to the sold half set

        elif current_price >= all_data1['target_price2'][s]:
            rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
            print(f"Second target price reached for {s}, selling all at market price.")
        
        elif current_price <= trailing_stop_price:
            rh.orders.order_sell_market(symbol=s, quantity=quantity, timeInForce='gfd')
            print(f"Trailing stop triggered for {s}, selling all at market price.")

    time.sleep(3600)


In [8]:
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime as dt
import time

username = 'jizhaobridgeport@gmail.com'
password = '12345shift'

def login():
    rh.login(username, password)

def get_stop(stock):# pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = ( today-datetime.timedelta(1)).strftime('%Y-%m-%d') 
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        tick = ticker
        last_day.index = [tick]
        last_day['stop_loss'] = (last_day['vol_down2'] +last_day['vol_down3'] )/2
        last_day['stop_loss_pct'] = (last_day['Close']- last_day['stop_loss'])/last_day['Close']*100
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] +last_day['Close'][-1] )/2

        return last_day
    
    
def get_trailing_stop_percentage(stock):
    stop_price = get_stop(stock)['stop_loss'][0]
    current_price = all_data1['price'][stock]
    trailing_percentage = (current_price - stop_price) / current_price
    return trailing_percentage * 0.2  # Use 20% of the calculated stop percentage

login()

sold_half = set()  # Track stocks that we have sold half of

while True:
    my_stocks = rh.build_holdings()
    df = pd.DataFrame(my_stocks).T
    df1 = df[['price', 'quantity', 'average_buy_price', 'percent_change']]
    stock = df1.index.tolist()
    all_data = pd.DataFrame()

    for ticker in stock:
        print(ticker)
        last_day = get_stop(ticker)
        all_data = pd.concat([all_data, last_day], axis=0)

    all_data = all_data[['stop_loss']]
    all_data1 = df1.merge(all_data, left_index=True, right_index=True)
    all_data1['price'] = all_data1['price'].astype(float)
    all_data1['pct_cha'] = ((all_data1['price'] - all_data1['stop_loss']) / all_data1['price']) * 100

    import random
    x = random.random()
    y = float((x + 5) / 100)
    z = float((10 - x) / 100)
    all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
    all_data1['target_price1'] = all_data1['average_buy_price'] * (1 + y)
    all_data1['target_price2'] = all_data1['average_buy_price'] * (1 + z)

    trailing_stop_percentages = {}
    for s in all_data1.index.tolist():
        trailing_stop_percentages[s] = get_trailing_stop_percentage(s)

    for s in all_data1.index.tolist():
        current_price = all_data1['price'][s]
        quantity = float(all_data1['quantity'][s])
        trailing_stop_price = current_price * (1 - trailing_stop_percentages[s])

        if current_price >= all_data1['target_price1'][s] and s not in sold_half:
            quantity1 = math.ceil(quantity / 2)  # sell half
            print(f"Would sell half of {s} at market price.")
            sold_half.add(s)  # Add the stock to the sold half set

        elif current_price >= all_data1['target_price2'][s]:
            print(f"Would sell all of {s} at market price.")
        
        elif current_price <= trailing_stop_price:
            print(f"Trailing stop would be triggered for {s}, selling all at market price.")

    time.sleep(3600)


400 Client Error: Bad Request for url: https://api.robinhood.com/fundamentals/?symbols=SBRCY
400 Client Error: Bad Request for url: https://api.robinhood.com/quotes/?symbols=SBRCY
DIS
BA
AMZN
GOOGL
ISRG
TSLA
MSFT
AAPL
U
JNJ
ADBE
TSM
CVS
BAC
SHOP
HD
GS
ETSY
UNH
INTU
ACN
Trailing stop would be triggered for DIS, selling all at market price.
Trailing stop would be triggered for BA, selling all at market price.
Trailing stop would be triggered for AMZN, selling all at market price.
Would sell half of GOOGL at market price.
Trailing stop would be triggered for ISRG, selling all at market price.
Would sell half of TSLA at market price.
Trailing stop would be triggered for AAPL, selling all at market price.
Trailing stop would be triggered for U, selling all at market price.
Trailing stop would be triggered for JNJ, selling all at market price.
Trailing stop would be triggered for TSM, selling all at market price.
Trailing stop would be triggered for CVS, selling all at market price.
Trailing

KeyboardInterrupt: 

In [ ]:
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime as dt
import time

username = 'jizhaobridgeport@gmail.com'
password = '12345shift'

def login():
    rh.login(username, password)

def get_stop(stock):# pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = ( today-datetime.timedelta(1)).strftime('%Y-%m-%d') 
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        tick = ticker
        last_day.index = [tick]
        last_day['stop_loss'] = (last_day['vol_down2'] +last_day['vol_down3'] )/2
        last_day['stop_loss_pct'] = (last_day['Close']- last_day['stop_loss'])/last_day['Close']*100
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] +last_day['Close'][-1] )/2

        return last_day
    
    
def get_trailing_stop_percentage(stock):
    stop_price = get_stop(stock)['stop_loss'][0]
    current_price = all_data1['price'][stock]
    trailing_percentage = (current_price - stop_price) / current_price
    return trailing_percentage * 0.2  # Use 20% of the calculated stop percentage

login()

sold_half = set()  # Track stocks that we have sold half of


while True:
    my_stocks = rh.build_holdings()
    df = pd.DataFrame(my_stocks).T
    df1 = df[['price', 'quantity', 'average_buy_price', 'percent_change']]
    stock = df1.index.tolist()
    all_data = pd.DataFrame()

    for ticker in stock:
        print(ticker)
        last_day = get_stop(ticker)
        all_data = pd.concat([all_data, last_day], axis=0)

    all_data = all_data[['stop_loss']]
    all_data1 = df1.merge(all_data, left_index=True, right_index=True)
    all_data1['price'] = all_data1['price'].astype(float)
    all_data1['pct_cha'] = ((all_data1['price'] - all_data1['stop_loss']) / all_data1['price']) * 100

    import random
    x = random.random()
    y = float((x + 5) / 100)
    z = float((10 - x) / 100)
    all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
    all_data1['target_price1'] = all_data1['average_buy_price'] * (1 + y)
    all_data1['target_price2'] = all_data1['average_buy_price'] * (1 + z)

    trailing_stop_percentages = {}
    for s in all_data1.index.tolist():
        trailing_stop_percentages[s] = get_trailing_stop_percentage(s)

    for s in all_data1.index.tolist():
        current_price = all_data1['price'][s]
        average_price = all_data1['average_buy_price'][s]
        quantity = float(all_data1['quantity'][s])
        trailing_stop_price = current_price * (1 - trailing_stop_percentages[s])
        loss_pct = (current_price - trailing_stop_price) / current_price * 100
        gain_pct = (current_price - average_price) / average_price * 100

        if current_price >= all_data1['target_price1'][s] and s not in sold_half:
            print(f"Would sell half of {s} at market price with a gain of {gain_pct:.2f}%.")
            sold_half.add(s)

        elif current_price >= all_data1['target_price2'][s]:
            print(f"Would sell all of {s} at market price with a gain of {gain_pct:.2f}%.")
        
        elif current_price <= trailing_stop_price:
            print(f"Trailing stop would be triggered for {s}, selling all at market price. Stop Price: ${trailing_stop_price:.2f}, Loss: {loss_pct:.2f}%.")

    time.sleep(3600)